# **Algoritmo Financiero**

Creador: **Juan Cassinerio** 

Master in finance/ Degree in Physics/ Data Scientist - Analyst  


### **Contenido**:

- 1. Introducción
- 2. Dataset y Analisis de Activos
    - 2.1. Conlusion y Recomendacion de inversion
- 3. MacroAnalisis
    - 3.1. Conlusion
- 4. Analisis de precio de activos a corto plazo
    - 4.1. Conlusion
- 5. Conclusion Final de Informe


## **1. Introduccion**
En este código, hemos creado una cartera de acciones personalizada utilizando Python. Un portfolio de Markowitz que maximiza los retornos mientras se minimiza el riesgo se ha creado. A la vez la diversificación de multiples activos puede reducir el riesgo al combinar activos que no están perfectamente correlacionados entre sí.

Los activos considerados son acciones Hemos utilizado datos históricos de múltiples activos (stock) presentes en índices **SP500, NASDAQ Composite y DOW JONES**, de los cuales se han importado datos históricos de "Yahoo Finance". 

Al final del informe se presentan los resultados y conclusiones financieras, presentando las 10 mejores activos.



## **2. Dataset y Analisis de Variables**

A continuación se importan precios de Mercado de acciones incluidas en los índices SP500 , Nasdaq y Dow Jones.

In [ ]:
!pip install yfinance

In [ ]:
import pandas as pd
import numpy as np
import yfinance as yf
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from sklearn.linear_model import LinearRegression
import plotly.graph_objs as go
import matplotlib.pyplot as plt
import scipy.optimize as optimize
import plotly.express as px
import plotly.graph_objects as go

#sp500_symbols = ['AAPL', 'MSFT', 'AMZN', 'FB', 'JPM', 'BAC', 'WFC', 'C', 'V', 'PG', 'MA', 'T', 'NVDA', 'HD', 'UNH', 'JNJ', 'DIS', 'PYPL', 'NFLX', 'XOM', 'KO', 'ADBE', 'ABBV', 'CVS', 'CRM', 'PEP', 'CMCSA', 'CAT', 'DHR', 'COST', 'MRK', 'MRNA', 'DOW', 'MMM', 'BMY', 'WMT', 'PFE', 'MCD', 'ABT', 'GE', 'JPM', 'AMGN', 'SLB', 'SPG', 'VZ', 'NKE', 'TSLA', 'PG', 'FDX', 'QCOM', 'ORCL', 'HON', 'MCO', 'MMM', 'MCHP', 'GS', 'COP', 'UNP', 'LIN', 'CCL', 'SYK', 'AVGO', 'BA', 'MMM', 'GILD', 'APD', 'CMI', 'LOW', 'EOG', 'ILMN', 'CL', 'VRTX', 'WBA', 'HUM', 'WM', 'MDLZ', 'WEC', 'MMC', 'EMR', 'D']

#nasdaq_symbols = ['AAPL', 'GOOG', 'AMZN', 'FB', 'TSLA', 'NVDA', 'PYPL', 'ADBE', 'NFLX', 'INTC', 'CMCSA', 'CSCO', 'PEP', 'TXN', 'AVGO', 'CHTR', 'COST', 'AMGN', 'SBUX', 'QCOM', 'BIIB', 'MDLZ', 'VRTX', 'ADP', 'GILD', 'BKNG', 'CERN', 'REGN', 'BIDU', 'CSX', 'MAR', 'EA', 'MELI', 'CDNS', 'SIRI', 'LULU', 'FISV', 'CTAS', 'VRSK', 'LBTYK', 'ADSK', 'NTES', 'INCY', 'PCAR', 'XLNX', 'FAST', 'WYNN', 'TTWO', 'IDXX', 'ALGN', 'MNST', 'MCHP', 'SWKS', 'CERN', 'CPRT', 'CDW', 'SPLK', 'CTSH', 'CHKP', 'VRSN', 'CDW', 'BMRN', 'ANSS', 'EXC', 'NTAP', 'SNPS', 'ULTA', 'NTGR']

#dowjones_symbols = ['AAPL', 'MSFT', 'V', 'WMT', 'HD', 'CRM', 'NKE', 'BA', 'KO', 'CAT', 'TRV', 'CVX', 'PG', 'JNJ', 'JPM', 'UNH', 'AXP', 'MMM', 'GS', 'MCD', 'CSCO', 'IBM', 'DIS', 'DOW', 'MRK', 'WBA', 'AMGN', 'VZ', 'HON', 'JNJ']



sp500_symbols = ['AAPL', 'GOOG', 'MSFT', 'AMZN', 'FB', 'JPM', 'BAC', 'WFC', 'C', 'V']
nasdaq_symbols = ['TSLA', 'NVDA', 'PYPL', 'INTC', 'ADBE', 'NFLX', 'AMGN', 'AVGO', 'TXN', 'QCOM']
dowjones_symbols = ['BA', 'MMM', 'PG', 'CSCO', 'GS', 'UNH', 'MCD', 'KO', 'JNJ', 'VZ']

tickers = sp500_symbols + nasdaq_symbols + dowjones_symbols
tickers = list(set(tickers))[:200]

print("List of 200 tickers:")
print(tickers)

tickers = sp500_symbols + nasdaq_symbols + dowjones_symbols

# Define the time periods
ten_years_ago = pd.Timestamp.now() - pd.DateOffset(years=10)
five_years_ago = pd.Timestamp.now() - pd.DateOffset(years=5)
two_years_ago = pd.Timestamp.now() - pd.DateOffset(years=2)

# Fetch the historical stock price data for the companies in the S&P 500, NASDAQ, and Dow Jones
data10 = yf.download(tickers, start=ten_years_ago, end=pd.Timestamp.now())['Adj Close']
data5 = yf.download(tickers, start=five_years_ago, end=pd.Timestamp.now())['Adj Close']
data2 = yf.download(tickers, start=two_years_ago, end=pd.Timestamp.now())['Adj Close']
data10 = data10.dropna(axis=1)
data5 = data5.dropna(axis=1)
data2 = data2.dropna(axis=1)

A continuacion se calcualn los retornos medios de los ultimos 10, 5 y 2 años de todas las acciones y se presentan aquellas con mejores **Ratio = Retorno/Volatilidad** en dichos 3 periodos.

In [14]:
returns10 = data10.pct_change().dropna()
mean_return10 = np.mean(returns10) * 252
volatility10 = np.std(returns10) * np.sqrt(252)
sharpe_ratio10 = mean_return10 / volatility10

returns5 = data5.pct_change().dropna()
mean_return5 = np.mean(returns5) * 252
volatility5 = np.std(returns5) * np.sqrt(252)
sharpe_ratio5 = mean_return5 / volatility5

returns2 = data2.pct_change().dropna()
mean_return2 = np.mean(returns2) * 252
volatility2 = np.std(returns2) * np.sqrt(252)
sharpe_ratio2 = mean_return2 / volatility2




##
results = pd.DataFrame({
    "Mean Return": mean_return10,
    "Volatility": volatility10,
    "Sharpe Ratio": sharpe_ratio10
}, index=tickers)
top10 = results.sort_values(by='Sharpe Ratio', ascending=False).head(10)


results = pd.DataFrame({
    "Mean Return": mean_return5,
    "Volatility": volatility5,
    "Sharpe Ratio": sharpe_ratio5
}, index=tickers)
top5 = results.sort_values(by='Sharpe Ratio', ascending=False).head(10)


results = pd.DataFrame({
    "Mean Return": mean_return2,
    "Volatility": volatility2,
    "Sharpe Ratio": sharpe_ratio2
}, index=tickers)
top2 = results.sort_values(by='Sharpe Ratio', ascending=False).head(10)


from IPython.display import display, HTML

# Display tables side by side with title
table_style = "<style>table{display: inline-block;margin-right: 20px;}</style>"
html_code = (f"<div style='display: flex; flex-direction: row;'>"
             f"<div style='margin-right: 50px;'>"
             f"<h2>Top 10 acciones con el mejor Ratio de los ultimos 10 años</h2>"
             f"{table_style}"
             f"{top10.to_html()}"
             f"</div>"
             f"<div style='margin-right: 50px;'>"
             f"<h2>Top 10 acciones con el mejor Ratio de los ultimos 5 años</h2>"
             f"{table_style}"
             f"{top5.to_html()}"
             f"</div>"
             f"<div>"
             f"<h2>Top 10 acciones con el mejor Ratio de los ultimos 2 años</h2>"
             f"{table_style}"
             f"{top2.to_html()}"
             f"</div>"
             f"</div>")

display(HTML(html_code))

# Add CSS to align tables horizontally
display(HTML("""
<style>
    .display-table {
        display: table;
        margin-left: auto;
        margin-right: auto;
    }
    .display-table > table {
        display: table-cell;
        vertical-align: middle;
    }
</style>
"""))


Los siguientes son las acciones que han tenido mejores rendimientos en los 3 periodos, indicando aquellas companias con rendimiento mas consistente.

In [15]:
tickers10 = set(results.sort_values(by='Sharpe Ratio', ascending=False).head(10).index)
tickers5 = set(results.sort_values(by='Sharpe Ratio', ascending=False).head(10).index)
tickers2 = set(results.sort_values(by='Sharpe Ratio', ascending=False).head(10).index)
tickers_common = list(tickers10 & tickers5 & tickers2)

print("Tickers presentes en las tres tablas:")
for ticker in tickers_common:
  print("- " + ticker)

Tickers presentes en las tres tablas:
- CSCO
- NVDA
- AAPL
- MSFT
- MCD
- KO
- AMGN
- AVGO
- PG
- UNH


A partir de este grupo optimo de acciones se crea un portfolio optimo que maximiza el Ratio = Retorno/Volatilidad, mientras a la vez tambien se diversifica la inversion. Se indica el porcentaje de que accion se debe invertir, tambien se define el retorno, volatilidad y ratio de dicho portfolio.

In [16]:
tickers = tickers_common
startdate = "2020-01-01"
data = yf.download(tickers, start=startdate)["Adj Close"]

log_returns = np.log(1 + data.pct_change())

port_returns = []
port_vols = []

for i in range(10000):
    num_assets = len(tickers)
    weights = np.random.random(num_assets)
    weights /= np.sum(weights)
    port_ret = np.sum(log_returns.mean() * weights) * 252
    port_var = np.sqrt(np.dot(weights.T, np.dot(log_returns.cov() * 252, weights)))
    port_returns.append(port_ret)
    port_vols.append(port_var)


def portfolio_stats(weights, log_returns):
    port_ret = np.sum(log_returns.mean() * weights) * 252
    port_var = np.sqrt(np.dot(weights.T, np.dot(log_returns.cov() * 252, weights)))
    sharpe = port_ret / port_var
    return {"Return": port_ret, "Volatility": port_var, "Sharpe": sharpe}


def minimize_sharpe(weights, log_returns):
    return -portfolio_stats(weights, log_returns)["Sharpe"]

port_returns = np.array(port_returns)
port_vols = np.array(port_vols)
sharpe = port_returns / port_vols

max_sr_vol = port_vols[sharpe.argmax()]
max_sr_ret = port_returns[sharpe.argmax()]

num_assets = len(tickers)

lower_bound = 0.01
upper_bound = 1.0

constraints = ({'type': 'eq', 'fun': lambda x: np.sum(x) - 1},
               {'type': 'ineq', 'fun': lambda x: x - lower_bound},
               {'type': 'ineq', 'fun': lambda x: upper_bound - x})

bounds = tuple((lower_bound, upper_bound) for x in range(num_assets))

initializer = num_assets * [1.0 / num_assets, ]

optimal_sharpe = optimize.minimize(
    minimize_sharpe,
    initializer,
    method="SLSQP",
    args=(log_returns,),
    bounds=bounds,
    constraints=constraints,
)

optimal_sharpe_weights = optimal_sharpe["x"].round(4)
optimal_stats = portfolio_stats(optimal_sharpe_weights, log_returns)

# Filtro para mantener los pesos que son al menos el 1% del portfolio
optimal_sharpe_weights_filtered = optimal_sharpe_weights[optimal_sharpe_weights >= 0.01]
tickers_filtered = tickers[:len(optimal_sharpe_weights_filtered)]

print("Retorno óptimo de la cartera: ", round(optimal_stats['Return']*100,4))
print("Volatilidad óptima de la cartera: ", round(optimal_stats['Volatility']*100,4))
print("Ratio Sharpe óptimo de la cartera: ", round(optimal_stats['Sharpe'],4))

print("\nComposición de la cartera:")
for i, ticker in enumerate(tickers):
    weight = optimal_sharpe_weights[i]*100
    print("{:<8}: {:>5.2f}%".format(ticker, weight))

# Gráfico de dispersión
fig_scatter = go.Figure()
fig_scatter.add_trace(go.Scatter(
    x=port_vols, y=port_returns,
    mode='markers',
    marker=dict(
        color=port_returns/port_vols,
        colorbar=dict(title="Ratio Sharpe (rf=0)"),
        colorscale="Blues",
        size=8,
        opacity=0.7,
        showscale=True
    ),
    text=[f"{ticker}: {round(weight*100, 2)}%" for ticker, weight in zip(tickers, optimal_sharpe_weights)],
    hoverinfo='text'
))
fig_scatter.add_trace(go.Scatter(
    x=[max_sr_vol], y=[max_sr_ret],
    mode='markers',
    marker=dict(
        color='red',
        size=12,
        opacity=1
    ),
    showlegend=False
))
fig_scatter.update_layout(
    xaxis_title='Volatilidad de la cartera',
    yaxis_title='Retorno de la cartera',
    margin=dict(l=0, r=0, t=30, b=0),
    height=400, width=2000
)
fig_scatter.show()

[*********************100%***********************]  10 of 10 completed


/usr/local/lib/python3.9/dist-packages/scipy/optimize/_optimize.py:353: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  warnings.warn("Values in x were outside bounds during a "


Retorno óptimo de la cartera:  30.8432
Volatilidad óptima de la cartera:  40.3464
Ratio Sharpe óptimo de la cartera:  0.7645

Composición de la cartera:
CSCO    : 13.14%
NVDA    :  1.00%
AAPL    :  1.00%
MSFT    :  1.00%
MCD     :  1.00%
KO      :  1.00%
AMGN    :  1.00%
AVGO    : 55.64%
PG      :  1.00%
UNH     : 24.21%


## 2.1. **Conlusión y Recomendación de inversión**

En este código, hemos creado una cartera de 10 acciones utilizando que maximiza el rendimiento, minimiza la volatilidad y asegura la inversion admitiendo diversificacion.


In [17]:
print("\nDesempeño proyectado de la cartera:")
print("Retorno proyectado de la cartera:     {:>5.2f}%".format(optimal_stats['Return']*100))
print("Volatilidad proyectado de la cartera: {:>5.2f}%".format(optimal_stats['Volatility']*100))

from IPython.display import display, HTML
import plotly.express as px

fig_pie = px.pie(
    values=optimal_sharpe_weights_filtered*100,
    names=tickers_filtered,
    title='Composición óptima de la cartera'
)
# Apply a style to the HTML object
html = '<div style="float:left;">' + fig_pie.to_html() + '</div>'
display(HTML(html))


Desempeño proyectado de la cartera:
Retorno proyectado de la cartera:     30.84%
Volatilidad proyectado de la cartera: 40.35%


Variacion hsitorica de precios de la acciones seleccionadas

In [35]:
import plotly.graph_objects as go

# Define the tickers to retrieve
tickers = tickers_filtered

# Define the start and end dates for the data
start_date = "2020-01-01"
end_date = "2023-03-13"

# Define the figure size
fig_size = (2000, 600)

# Calculate the number of rows and columns for the grid
n_rows = 2
n_cols = 5

# Loop through the tickers and plot their closing prices on a grid of charts
fig = make_subplots(rows=n_rows, cols=n_cols, subplot_titles=tickers)
for i, ticker in enumerate(tickers_filtered):
    # Retrieve the historical price data of the ticker
    data = yf.download(ticker, start=start_date, end=end_date)
    # Add the trace for the closing price of the ticker to the figure
    row = (i // n_cols) + 1
    col = (i % n_cols) + 1
    fig.add_trace(
        go.Scatter(
            x=data.index,
            y=data["Close"],
            name=ticker
        ),
        row=row,
        col=col
    )
    # Add the trace for the rolling mean of the closing price of the ticker to the figure
    fig.add_trace(
        go.Scatter(
            x=data.index,
            y=data["Close"].rolling(30).mean(),
            name=ticker + " (Rolling Mean)"
        ),
        row=row,
        col=col
    )
    
# Update the layout of the figure
fig.update_layout(
    title="Price Charts of Selected Tickers",
    width=fig_size[0],
    height=fig_size[1],
    showlegend=False
)
fig.show()


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed


## 3. **MacroAnalisis**

Se descargan los datos de los índices bursátiles S&P 500, Nasdaq Composite y Dow Jones Industrial Average, así como la tasa de fondos federales (Fed Funds) desde el 1 de diciembre de 2021 hasta el 5 de marzo de 2023.

In [49]:
import pandas as pd
import numpy as np
import yfinance as yf
import matplotlib.pyplot as plt
import pandas_datareader.data as web

tickers = ["^GSPC", "^IXIC", "^DJI"]
start_date = "2021-12-01"
end_date = "2023-03-05"
data = yf.download(tickers, start=start_date, end=end_date)
fedfunds = web.DataReader("FEDFUNDS", "fred", start_date, end_date)

#######
index = data['Adj Close'].mean(axis=1)
df['index']=index
df['FEDFUNDS'] = fedfunds['FEDFUNDS']
df = df[['index', 'FEDFUNDS']].resample('M').mean()
df['Month'] = df.index.strftime('%Y-%m')
df['Month'] = pd.to_datetime(df['Month'], format='%Y-%m')
df=df.dropna()
#df.dtypes
df

[*********************100%***********************]  3 of 3 completed


index  FEDFUNDS      Month
Date                                         
2021-12-31  18596.846103      0.08 2021-12-01
2022-02-28  17661.063057      0.08 2022-02-01
2022-03-31  17348.089624      0.20 2022-03-01
2022-04-30  17366.816357      0.33 2022-04-01
2022-06-30  15588.192856      1.21 2022-06-01
2022-07-31  15689.894792      1.68 2022-07-01
2022-08-31  16579.462788      2.33 2022-08-01
2022-09-30  15300.976667      2.56 2022-09-01
2022-11-30  16103.028316      3.78 2022-11-01
2022-12-31  16077.878007      4.10 2022-12-01
2023-02-28  16504.338610      4.57 2023-02-01

In [50]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots

fig = make_subplots(rows=1, cols=2, subplot_titles=('FEDFUNDS', 'index'))

fig.add_trace(go.Scatter(x=df['Month'], y=df['FEDFUNDS'], mode='markers', name='Population'), row=1, col=1)
fig.add_trace(go.Scatter(x=df['Month'], y=df['FEDFUNDS'], mode='lines', line=dict(dash='dash', color='red'), showlegend=False), row=1, col=1)

fig.add_trace(go.Scatter(x=df['Month'], y=df['index'], mode='markers', name='Working Force'), row=1, col=2)
fig.add_trace(go.Scatter(x=df['Month'], y=df['index'], mode='lines', line=dict(dash='dash', color='red'), showlegend=False), row=1, col=2)
fig.show()

Luego se grafican los datos y se realiza una regresión lineal entre la tasa de fondos federales y el índice compuesto de las tres bolsas de valores mencionadas. La regresión lineal sugiere que la tasa de fondos federales tiene una influencia significativa en el mercado de valores.

In [51]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df['FEDFUNDS'], y=df['index'], mode='markers', name='GDP'))
fig.update_layout(
    width=800,
    height=500
)
fig.show()

from sklearn.metrics import r2_score, mean_absolute_error
from sklearn.linear_model import LinearRegression

# Drop NaN values from the DataFrame
df = df.dropna()

# Create the x and y variables
x = df['FEDFUNDS']
y = df[['index']]

# Reshape x to a 2D array with a single feature
x = x.values.reshape(-1, 1)

# Fit the linear regression model
linear2 = LinearRegression()
model2 = linear2.fit(x, y)

# Calculate the R-squared value and make predictions
r_sq2 = model2.score(x, y)
y_pred = model2.predict(x)

print("Correlation:", r_sq2)

Correlation: 0.3622348532331098


Se utilizó una curva de ajuste cuadrático para predecir el valor de la tasa de fondos federales para los próximos 6 meses a partir del último valor registrado. Según los resultados, se observa una correlación entre la tasa de fondos federales y el índice compuesto de las bolsas de valores.


In [72]:
# Define the time step
x = df['Month']
y = df['FEDFUNDS']
x1 = df['Month'].iloc[-1]


#amount of back points used #################

n=6
x_fit = pd.to_numeric((x - pd.Timestamp("1970-01-01")) // pd.Timedelta('1s')).astype(float)[n:]
y_fit = y[n:]

def func(x,a,b,c):
    return c*x**2 + b*x + a
popt3, _ = curve_fit(func, x_fit, y_fit)
ym = func(x_fit, *popt3)
print("Correlation: %.2f" % r2_score(ym, y_fit))

# Perform extrapolation for the next step, months m point on future
m=6
extrapolated_data = []
for i in range(m+1):
    next_x = (x1 + pd.DateOffset(months=i) - pd.Timestamp("1970-01-01")) // pd.Timedelta('1s')

    next_y = func(next_x, *popt3) 
    extrapolated_data.append([next_x, next_y])
ex= pd.DataFrame(extrapolated_data, columns=['x', 'y'])
ex['x'] = pd.to_datetime(ex['x'], unit='s')

fig = go.Figure()
fig.add_trace(go.Scatter(x=ex['x'], y=ex['y'], mode='markers', name='extrapolation data'))
fig.add_trace(go.Scatter(x=ex['x'], y=ex['y'], mode='lines', line=dict(dash='dash', color='red'), showlegend=False))
fig.add_trace(go.Scatter(x=x, y=y, mode='markers', name='present data'))
fig.add_trace(go.Scatter(x=x, y=y, mode='lines', line=dict(dash='dash', color='red'), showlegend=False))
fig.update_layout(
    width=700,
    height=400
)
fig.show()

Correlation: 0.98


In [75]:
x = ex['y'].values.reshape(-1, 1)
y_pred = model2.predict(x)
df_pred = pd.DataFrame(y_pred, columns=['index'])
df_pred['year'] = ex['x']

fig = go.Figure()
fig.add_trace(go.Scatter(x=df['Month'], y=df['index'], mode='markers', name='present data'))
fig.add_trace(go.Scatter(x=df['Month'], y=df['index'], mode='lines', line=dict(dash='dash', color='red'), showlegend=False))

fig.add_trace(go.Scatter(x=df_pred['year'], y=df_pred['index'], mode='markers', name='extrapolation data'))
fig.add_trace(go.Scatter(x=df_pred['year'], y=df_pred['index'], mode='lines', line=dict(dash='dash', color='red'), showlegend=False))

# Get the index of the row with the minimum value
min_idx = df_pred['index'].idxmin()

# Get the year and index values at the minimum index
min_year = df_pred.loc[min_idx, 'year']
min_index = df_pred.loc[min_idx, 'index']

# Print the minimum year and index values
print(f"The extrapolated point with the minimum value is ({min_year}, {min_index})")

fig.update_layout(
    width=1400,
    height=400
)
fig.show()

The extrapolated point with the minimum value is (2023-05-01 00:00:00, 15528.04135839506)


## 3.2. **Conclusion**
Según la gráfica de extrapolación, el promedio entre los indices **SP500, NASDAQ Composite y DOW JONES** continuará disminuyendo al canzando un minimo en aproximadamentre 4 meses, lo que indica que el promedio de los activos presentes en dichos indices comenzaran a aumentar después de ese punto.



## 3.2. **Analisis de precio de activos a corto plazo**



## 3.2. **Conclusion**


 ## 5. **Conclusion Final de Informe**

